In [74]:
# Imports
import sys
import os
import json
import pandas as pd
import matplotlib.pyplot as plt 
# is it significant
import numpy as np

In [2]:
#HIV_RT
#tag = "HIV_RT"
#analysis_type = "empirical"
#path = "../Results/HIV_RT"
#path = os.path.join("..", "Results", tag)
#print("#", path)
#files = [path + "/" + f.name for f in os.scandir(path) if f.name.endswith(".FEL.json")]
#output_header = "MESSI_" + tag + "_" + analysis_type + "_FEL"

# IAV Chen
#path = "../../Test_TN93_algo_subsamples"
path = os.path.join("..", "Results", "IAV_Chen")
#files = [path + "/" + f.name for f in os.scandir(path) if f.name.endswith(".MEME.json")]
files = [os.path.join(path, f.name) for f in os.scandir(path) if f.name.endswith(".MEME.json")]
#output_header = "../../Plots/BDNF_TN93Algo_MEME_InternalBranches.png"
output_header = "IAV_Chen"

#files

In [43]:
# Main -------------------------------------------------
data_dict = {}
pvalue_threshold = 0.1
count = 1
Ps = []
for filename in files:
    if os.stat(filename).st_size == 0: 
        print("# ERROR:", filename)
        continue
    #end if
    with open(filename, "r") as fh:
        json_data = json.load(fh)
    #end with
    
    num_seqs = json_data["input"]["number of sequences"]
    
    MLE = json_data["MLE"]["content"]["0"]
    
    for n, item in enumerate(MLE):
        alpha = item[0]
        beta_minus = item[1]
        pvalue = item[6]
    
        data_dict[count] = {"Filename":filename.split("/")[-1],
                                "num_seqs": num_seqs,
                                "Site": str(n+1),
                                "alpha": alpha,
                                "beta_minus": beta_minus,
                                "pvalue": pvalue}
        
        if float(pvalue) <= 0.1:
            Ps.append(str(n+1))
        count += 1
    #count += 1
#end for

In [44]:
df = pd.DataFrame.from_dict(data_dict, orient='index')
df.sort_values(by=['num_seqs'], ascending=True, inplace=True)
df = df.reset_index(drop=True)
df.index += 1
df

Filename  num_seqs Site  \
1      ..\Results\IAV_Chen\IAV_Chen.fasta.3.subsample...         3    1   
2      ..\Results\IAV_Chen\IAV_Chen.fasta.3.subsample...         3  225   
3      ..\Results\IAV_Chen\IAV_Chen.fasta.3.subsample...         3  224   
4      ..\Results\IAV_Chen\IAV_Chen.fasta.3.subsample...         3  223   
5      ..\Results\IAV_Chen\IAV_Chen.fasta.3.subsample...         3  222   
...                                                  ...       ...  ...   
27303  ..\Results\IAV_Chen\IAV_Chen.fasta.85.subsampl...        85  223   
27304  ..\Results\IAV_Chen\IAV_Chen.fasta.85.subsampl...        85  224   
27305  ..\Results\IAV_Chen\IAV_Chen.fasta.85.subsampl...        85  225   
27306  ..\Results\IAV_Chen\IAV_Chen.fasta.85.subsampl...        85  227   
27307  ..\Results\IAV_Chen\IAV_Chen.fasta.85.subsampl...        85    2   

            alpha  beta_minus    pvalue  
1      159.000000    0.000000  0.666667  
2      159.000000    0.000000  0.666667  
3       10.019639    0.000000  0.666667  
4        0.000000    0.000000  1.000000  
5        0.000000    0.000000  1.000000  
...           ...         ...       ...  
27303    1.643903    0.000000  0.666667  
27304    0.672579    0.000000  0.666667  
27305    2.999358    0.597836  0.666667  
27306    4.453874    0.457692  0.666667  
27307    1.297135    0.052181  0.602868  

[27307 rows x 6 columns]

## Plots

In [45]:
import altair as alt
from vega_datasets import data
alt.data_transformers.disable_max_rows()
source = df

a = set(df["Site"])
b = sorted(list(a), reverse=False)
c = [str(i) for i in b]
d = sorted(list(c), key=int, reverse=False)
#y=alt.Y('PositiveSite', sort=d)
#extent='min-max'
box1 = alt.Chart(source).mark_boxplot(extent='min-max', size=5).encode(
    x=alt.X('Site', sort=d),
    y=alt.Y("alpha", scale=alt.Scale(domain=[0, 20], clamp=True))
).properties(
    width=2000,
    height=300
).configure_axis(
    labelFontSize=10,
    titleFontSize=10
)

box1

alt.Chart(...)

In [46]:
box2 = alt.Chart(source).mark_boxplot(extent='min-max', size=5).encode(
    x=alt.X('Site', sort=d),
    y=alt.Y("beta", scale=alt.Scale(domain=[0, 20], clamp=True))
).properties(
    width=2000,
    height=300
).configure_axis(
    labelFontSize=10,
    titleFontSize=10
)
box2


ValueError: beta encoding field is specified without a type; the type cannot be inferred because it does not match any column in the data.

alt.Chart(...)

## Facets/ Site plots

In [47]:
Ps = list(set(Ps))

In [48]:
# Only for these sites

In [75]:
#df_dN_subset = df_dN[df_dN["Site"] in Ps]
df_subset = df[df['Site'].isin(Ps)]
df_subset['pvalue_sig'] = np.where(df_subset['pvalue'] <= 0.1, True, False)
df_subset

<ipython-input-75-c09292a2e333>:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_subset['pvalue_sig'] = np.where(df_subset['pvalue'] <= 0.1, True, False)


Filename  num_seqs Site  \
9      ..\Results\IAV_Chen\IAV_Chen.fasta.3.subsample...         3  226   
45     ..\Results\IAV_Chen\IAV_Chen.fasta.3.subsample...         3  182   
75     ..\Results\IAV_Chen\IAV_Chen.fasta.3.subsample...         3  193   
224    ..\Results\IAV_Chen\IAV_Chen.fasta.3.subsample...         3    3   
255    ..\Results\IAV_Chen\IAV_Chen.fasta.3.subsample...         3  138   
...                                                  ...       ...  ...   
27052  ..\Results\IAV_Chen\IAV_Chen.fasta.85.subsampl...        85  138   
27082  ..\Results\IAV_Chen\IAV_Chen.fasta.85.subsampl...        85    3   
27231  ..\Results\IAV_Chen\IAV_Chen.fasta.85.subsampl...        85  193   
27261  ..\Results\IAV_Chen\IAV_Chen.fasta.85.subsampl...        85  182   
27288  ..\Results\IAV_Chen\IAV_Chen.fasta.85.subsampl...        85  226   

          alpha  beta_minus    pvalue  pvalue_sig  
9      2.212741    2.212741  0.424098       False  
45     0.000000    0.000000  1.000000       False  
75     0.000000    0.000000  0.407717       False  
224    0.000000    0.000000  0.106035       False  
255    0.000000    0.000000  1.000000       False  
...         ...         ...       ...         ...  
27052  0.000000    0.000000  0.064901        True  
27082  0.927809    0.039638  0.557742       False  
27231  0.000000    0.000000  0.011848        True  
27261  1.859162    1.086629  0.666667       False  
27288  0.000000    0.000000  0.002292        True  

[1079 rows x 7 columns]

In [52]:
source = df_subset

a = set(df["Site"])
b = sorted(list(a), reverse=False)
c = [str(i) for i in b]
d = sorted(list(c), key=int, reverse=True)

alt.Chart(source).mark_boxplot(extent='min-max', size=5).encode(
    y=alt.Y('Site', sort=d),
    x=alt.X("alpha", scale=alt.Scale(domain=[0, 10], clamp=True))
).properties(
    width=2000,
    height=300
).configure_axis(
    labelFontSize=10,
    titleFontSize=10
)


alt.Chart(...)

In [53]:
source = df_subset

a = set(df["Site"])
b = sorted(list(a), reverse=False)
c = [str(i) for i in b]
d = sorted(list(c), key=int, reverse=True)

alt.Chart(source).mark_boxplot(extent='min-max', size=5).encode(
    y=alt.Y('Site', sort=d),
    x=alt.X("beta", scale=alt.Scale(domain=[0, 10], clamp=True))
).properties(
    width=2000,
    height=300
).configure_axis(
    labelFontSize=10,
    titleFontSize=10
)

ValueError: beta encoding field is specified without a type; the type cannot be inferred because it does not match any column in the data.

alt.Chart(...)

In [54]:
# Custom, for a single site, dS and dN across num_seqs (x), and y (the values).a

source = df_subset

alt.Chart(source).mark_point().encode(
    alt.X(alt.repeat("column"), type='quantitative'),
    alt.Y(alt.repeat("row"), type='quantitative'),
    color='Site:N'
).properties(
    width=200,
    height=200
).repeat(
    row=['alpha', 'beta'],
    column=['num_seqs']
).interactive()

alt.RepeatChart(...)

In [55]:
alt.Chart(source).mark_point().encode(
    x=alt.X('num_seqs', sort=d),
    y='alpha:Q',
    color='Site:N'
).properties(
    width=200,
    height=200
).facet(
    column='Site:N'
).configure_axis(
    labelFontSize=20,
    titleFontSize=20
)


alt.FacetChart(...)

In [56]:
import altair as alt
from vega_datasets import data

alt.Chart(source).mark_line(size=5).encode(
    x=alt.X('num_seqs', sort=d),
    y='beta',
    color='Site:N'
).properties(
    width=200,
    height=200
).facet(
    column='Site'
).configure_axis(
    labelFontSize=20,
    titleFontSize=20
)


ValueError: beta encoding field is specified without a type; the type cannot be inferred because it does not match any column in the data.

alt.FacetChart(...)

In [57]:
import altair as alt
from vega_datasets import data

source = df_subset


L1 = alt.Chart(source).mark_line(size=4).encode(
    x='num_seqs',
    y=alt.Y(
        'beta',
        title='beta',
        axis=alt.Axis(format='~s')
    ),color='Site',
    facet=alt.Facet(
        'Site', columns=5,
        header=alt.Header(labelFontSize=18)
    ),
).properties(
    title='beta rate properties by SIte',
    width=200,
    height=200
).configure_title(fontSize=24)


L2 = alt.Chart(source).mark_line(size=4).encode(
    x='num_seqs',
    y=alt.Y(
        'alpha',
        title='alpha',
        axis=alt.Axis(format='~s')
    ), color='Site',
    facet=alt.Facet(
        'Site', columns=5,
        header=alt.Header(labelFontSize=18)
    ),
).properties(
    title='alpha rate properties by SIte',
    width=200,
    height=200
).configure_title(fontSize=24)

#alt.concat(*(
#    alt.layer(L1, L2, title=f"Site = {val}").transform_filter(alt.datum.Site == val).resolve_scale(y='independent',x='independent')#
#    for val in source.Site.unique()
#))
L1

ValueError: beta encoding field is specified without a type; the type cannot be inferred because it does not match any column in the data.

alt.Chart(...)

In [58]:
L2

alt.Chart(...)

In [72]:
source = df_subset

chart = alt.Chart(source).mark_line(size=4).encode(
    x='num_seqs',
    y=alt.Y(
        'pvalue',
        title='pvalue',
        axis=alt.Axis(format='~s')
    ),
    color='Site',
    facet=alt.Facet(
        'Site', columns=5,
        header=alt.Header(labelFontSize=18)
    ),
).properties(
    title='pvalue properties by Site',
    width=200,
    height=200
).configure_title(
    fontSize=24)

line = alt.Chart(pd.DataFrame({'y': [0.1]})).mark_rule().encode(y='y')

chart

alt.Chart(...)

In [81]:
source = df_subset

chart = alt.Chart(source).mark_point(size=8).encode(
    x='num_seqs',
    y=alt.Y(
        'pvalue',
        title='pvalue',
        axis=alt.Axis(format='~s')
    ),
    color='pvalue_sig',
    facet=alt.Facet(
        'Site', columns=5,
        header=alt.Header(labelFontSize=18)
    ),
).properties(
    title='pvalue properties by Site',
    width=200,
    height=200
).configure_title(
    fontSize=24)

chart

alt.Chart(...)